<center><img src="logo.png" /></center>

# <center>Avey: A High-Level Overview</center>

## Table of Contents

* [Introduction](#intro)
* [Cases](#cases)
* [Metrics and Calculations](#metrics)
* [Results](#results)

<p>


## Introduction<a class="anchor" id="intro"></a>
<p>This notebook is a supplement of the <a href="https://www.medrxiv.org/content/10.1101/2022.03.08.22272076v1.full"> paper </a> we are submitting. In this notebook, we share all the cases (after manual cleaning and matching) that we analysed and their results. We also share results from multiple experiments, few of which were discussed in the paper.</p>


#### Load data

In [1]:
EXPERIMENT_TAG = 'avey'
# EXPERIMENT_TAG = 'harvard'

In [2]:
# load data

import json
import pandas as pd
from collections import defaultdict
import math
import numpy as np
import os

def loadData(fileName):
    '''Loading data from result files'''
    with open(f'{fileName}.json', 'r', encoding='utf-8') as file:
        data = json.load(file)
        return data

def normalize(cases):
    '''make all the ddx list of a case of the same length by padding with None'''
    for case in cases.values():
        maxLen = max(len(result) for result in case.values())
        for result in case.values():
            result += [None]*(maxLen-len(result))

        assert len(set(len(result) for result in case.values())) == 1
    
    return cases

def getDataframe(case):
    '''Convert each test case into a dataframe'''
    caseLen = len(next(iter(case.values())))
    if EXPERIMENT_TAG == 'avey':
        gold = ['gold','gold_old']
    else:
        gold = ['gold']
    return pd.DataFrame(
        case,
        columns=[*gold,
        *sorted([key for key in case.keys() if 'gold' not in key and 'doctor' not in key]),
        *sorted([key for key in case.keys() if 'gold' not in key and 'doctor' in key]),
        ],
        index= list(range(1,1+caseLen))
        )


In [3]:
# We need to make all the differentials of the same length to ease comparison
# We pad the lists with None
data = loadData('data/allResults')
if EXPERIMENT_TAG != 'harvard':
    dataOld = loadData('data/allResults_old')

for caseNum in data:
    for app in data[caseNum]:
        # removing empty strings
        data[caseNum][app] = [r for r in data[caseNum][app] if r]

    # adding old results
    if EXPERIMENT_TAG != 'harvard' and caseNum in dataOld:
        for app in dataOld[caseNum]:
            data[caseNum][f"{app}_old"] = [r for r in dataOld[caseNum][app] if r]

normalizedData = normalize(data)
if EXPERIMENT_TAG == 'harvard':
    cases = {int(id): getDataframe(case) for id, case in normalizedData.items() if int(id)>500}
else:
    cases = {int(id): getDataframe(case) for id, case in normalizedData.items() if int(id)<=500}

display(f'We have {len(cases)} cases in the experiment.')

'We have 485 cases in the experiment.'

In [4]:
caseClassificationOld = loadData("data/case-classification_old")
failures_temp = (
    pd.read_excel("data/AppTest-2024-02-06.xlsx")
    .dropna(subset=["invalid_code"])
    .groupby(["medical_app", "invalid_code"])["case_study"]
    .agg(set)
    .reset_index()
).set_index(["medical_app", "invalid_code"]).to_dict('index')

failures = defaultdict(dict)
for (app, err), failedCases in  failures_temp.items():
    failures[app][err] = failedCases['case_study']

for app in failures:
    failures[app]["session failed"] = set()
    for err, failedCases in failures[app].items():
        if err != 'NDX':
            failures[app]["session failed"] |= failedCases

    failures[app]["no disease found"] = failures[app]["NDX"]
    del failures[app]["NDX"]

failures = dict(failures)

if EXPERIMENT_TAG == 'avey':
    for app, data in caseClassificationOld['apps'].items():
        failures[app] = data 
# failures

In [5]:
df = pd.read_excel(
    "data/Results - Apps performance - team copy.xlsx",
    sheet_name=(
        "Harvard cases"
        if EXPERIMENT_TAG == "harvard"
        else "Detailed diseases coverage - 50"
    ),
    index_col=1,
).dropna(subset=["Common vs Less common"])["Common vs Less common"]

df.index = [int(str(i).replace('#','')) for i in df.index]
caseClassification = {
    'common':set(),
    'less common':set(),
    'apps':failures,
}
for case_num, typ in df.items():
    if typ == 'Common':
        caseClassification['common'].add(case_num)
    else:
        caseClassification['less common'].add(case_num)

assert set(cases.keys()).issubset(
    caseClassification["common"] | caseClassification["less common"]
), f'Vignette results have extra ids that are not in classification {set(cases.keys()) - (caseClassification["common"] | caseClassification["less common"])}'

print(f'We have {len(caseClassification["common"])} common diseases and {len(caseClassification["less common"])} less common diseases')
display('App v Error code: Case Count')
pd.DataFrame({app: {err: len(v) for err, v in errs.items()} for app, errs in caseClassification["apps"].items()}).transpose()

We have 272 common diseases and 228 less common diseases


c:\Users\swapn\anaconda3\envs\mlflow\Lib\site-packages\openpyxl\worksheet\_reader.py:329: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


'App v Error code: Case Count'

MAC  OTH  session failed  no disease found  A01   CNA   A16  \
Avey           3.0  1.0             4.0              29.0  NaN   NaN   NaN   
Avey v2        NaN  1.0             1.0              13.0  NaN   NaN   NaN   
Buoy           7.0  7.0            23.0               3.0  7.0   2.0   NaN   
Healthily      NaN  NaN            64.0              18.0  NaN   5.0  59.0   
K Health      10.0  3.0            95.0               1.0  NaN  19.0   NaN   
Mediktor       1.0  NaN             1.0              41.0  NaN   NaN   NaN   
Symptomate     1.0  NaN             9.0              17.0  NaN   NaN   NaN   
WebMD          NaN  NaN             6.0               1.0  5.0   1.0   NaN   
Avey_old       NaN  NaN             0.0               2.0  NaN   NaN   NaN   
Ada_old        NaN  NaN             0.0               0.0  NaN   NaN   NaN   
Babylon_old    NaN  NaN            15.0             352.0  NaN   NaN   NaN   
Buoy_old       NaN  NaN            10.0              75.0  NaN   NaN   NaN   
K health_old   NaN  NaN            53.0               2.0  NaN   NaN   NaN   
WebMD_old      NaN  NaN             3.0               3.0  NaN   NaN   NaN   

               A18  
Avey           NaN  
Avey v2        NaN  
Buoy           NaN  
Healthily      NaN  
K Health      63.0  
Mediktor       NaN  
Symptomate     8.0  
WebMD          NaN  
Avey_old       NaN  
Ada_old        NaN  
Babylon_old    NaN  
Buoy_old       NaN  
K health_old   NaN  
WebMD_old      NaN

## TODO: NEED TO REMOVE DUPLICATE TESTS AND VERIFY THE NUMBER OF ERRORS

<p>

### Let us have a look at all the cases. <a class="anchor" id="cases"></a>
The cases have been labelled common and less common by our doctors. We have also labelled the cases with apps that failed on them.

In [6]:
from IPython.display import display

for caseNum, case in cases.items():
    isCommonString = 'common' if caseNum in caseClassification['common'] else 'less common'
    sessionFailed, noDiseaseFound = ([], [])
    for app, failedCases in caseClassification['apps'].items():
        if caseNum in failedCases['session failed']:
            sessionFailed.append(app)
        elif caseNum in failedCases['no disease found']:
            noDiseaseFound.append(app)

    print(f'Case number {caseNum} ({isCommonString})')
    if sessionFailed:
        print(
            f'Session failed to start for: {", ".join(sessionFailed)}.')
    if noDiseaseFound:
        print(
            f'No diseases were found for: {", ".join(noDiseaseFound)}.')
    display(case)
    case.to_excel(f'individual_case_outputs/{EXPERIMENT_TAG}/{caseNum}.xlsx')
    print('\n'*2)


Case number 1 (common)
No diseases were found for: Babylon_old.


gold          gold_old               Ada               Ada_old  \
1  acute bronchitis  acute bronchitis  acute bronchitis      acute bronchitis   
2       common cold       common cold       common cold                asthma   
3         influenza         influenza  acute laryngitis        whooping cough   
4            asthma            asthma          covid 19             pneumonia   
5              None              None         pneumonia  mycoplasma pneumonia   
6              None              None              None                  None   
7              None              None              None                  None   
8              None              None              None                  None   

               Avey                  Avey v2             Avey_old Babylon_old  \
1  acute bronchitis         acute bronchitis     acute bronchitis        None   
2          covid 19     bacterial tracheitis          common cold        None   
3       common cold              common cold            pneumonia        None   
4   cystic fibrosis  foreign body aspiration      pulmonary edema        None   
5         pneumonia         acute laryngitis           laryngitis        None   
6              None                     None  tonsillopharingitis        None   
7              None                     None                 None        None   
8              None                     None                 None        None   

               Buoy          Buoy_old  ...                 Mediktor  \
1  acute bronchitis  acute bronchitis  ...                   asthma   
2      benign cough            asthma  ...         acute bronchitis   
3         influenza      benign cough  ...  hyperresponsive bronchi   
4              None              None  ...                     None   
5              None              None  ...                     None   
6              None              None  ...                     None   
7              None              None  ...                     None   
8              None              None  ...                     None   

            Symptomate              WebMD                 WebMD_old  \
1     acute bronchitis          pneumonia                    asthma   
2  tonsillopharyngitis          influenza          acute bronchitis   
3          common cold             asthma  coronavirus disease 2019   
4     acute laryngitis        common cold                 influenza   
5      acute sinusitis  chronic sinusitis         chronic sinusitis   
6                 None     whooping cough                      None   
7                 None   acute bronchitis                      None   
8                 None        lung cancer                      None   

                 doctor_MA            doctor_MA_old doctor_NJ  \
1  gastroesophageal reflux  gastroesophageal reflux    asthma   
2          post nasal drip          post nasal drip      None   
3         acute bronchitis         acute bronchitis      None   
4                     None                     None      None   
5                     None                     None      None   
6                     None                     None      None   
7                     None                     None      None   
8                     None                     None      None   

                                       doctor_NJ_old              doctor_TH  \
1  reactive airway disease with superimposed infe...  post infectious cough   
2                                               None       acute bronchitis   
3                                               None                   None   
4                                               None                   None   
5                                               None                   None   
6                                               None                   None   
7                                               None                   None   
8                                               None     




Case number 2 (common)
No diseases were found for: Babylon_old, Buoy_old.


gold               gold_old  \
1        unstable angina        unstable angina   
2  myocardial infarction  myocardial infarction   
3          stable angina          stable angina   
4   pericardial effusion   pericardial effusion   
5                   None                   None   
6                   None                   None   
7                   None                   None   
8                   None                   None   

                                       Ada  \
1                          unstable angina   
2                    myocardial infarction   
3        acute biventricular heart failure   
4               acute aortic regurgitation   
5  obstructive hypertrophic cardiomyopathy   
6                                     None   
7                                     None   
8                                     None   

                                 Ada_old                   Avey  \
1                        unstable angina        unstable angina   
2                         collapsed lung  myocardial infarction   
3                  myocardial infarction          stable angina   
4  chronic obstructive pulmonary disease      aortic dissection   
5                          stable angina        costochondritis   
6                                   None                   None   
7                                   None                   None   
8                                   None                   None   

                 Avey v2               Avey_old Babylon_old  \
1        unstable angina        unstable angina        None   
2     pulmonary embolism  myocardial infarction        None   
3  myocardial infarction          stable angina        None   
4   pericardial effusion         varient angina        None   
5      aortic dissection                   None        None   
6                   None                   None        None   
7                   None                   None        None   
8                   None                   None        None   

                  Buoy Buoy_old  ...               Mediktor  \
1      unstable angina     None  ...  myocardial infarction   
2  atypical chest pain     None  ...        unstable angina   
3   heart valve issues     None  ...                   None   
4                 None     None  ...                   None   
5                 None     None  ...                   None   
6                 None     None  ...                   None   
7                 None     None  ...                   None   
8                 None     None  ...                   None   

              Symptomate                                           WebMD  \
1        unstable angina                           myocardial infarction   
2  myocardial infarction                                 unstable angina   
3                   None                              pulmonary embolism   
4                   None                        congestive heart failure   
5                   None                             atrial fibrillation   
6                   None  heart failure with preserved ejection fraction   
7                   None                        takotsubo cardiomyopathy   
8                   None                                 heart burn gerd   

               WebMD_old              doctor_MA          doctor_MA_old  \
1  myocardial infarction          stable angina          stable angina   
2            broken ribs        unstable angina        unstable angina   
3        costochondritis  myocardial infarction  myocardial infarction   
4         heartburn/gerd                   None                   None   
5        unstable angina                   None                   None   
6     pulmonary embolism                   None                   None   
7                   None                   None                   None   
8                   None                   None                   None   

               doctor_NJ          doctor_NJ_old      




Case number 3 (less common)
No diseases were found for: Babylon_old, Buoy_old.


...

gold               gold_old                    Ada  \
1  intercostal neuralgia  intercostal neuralgia        costochondritis   
2               shingles               shingles        pectoral strain   
3        costochondritis        costochondritis    intercostal myalgia   
4                   None                   None      chest wall injury   
5                   None                   None  intercostal neuralgia   
6                   None                   None                   None   
7                   None                   None                   None   
8                   None                   None                   None   

                     Ada_old                   Avey                Avey v2  \
1               chest injury  intercostal neuralgia  intercostal neuralgia   
2  intercostal muscle strain        costochondritis        costochondritis   
3            pectoral strain           fibromyalgia           fibromyalgia   
4                       None  myocardial infarction  myocardial infarction   
5                       None                   None                   None   
6                       None                   None                   None   
7                       None                   None                   None   
8                       None                   None                   None   

                Avey_old Babylon_old                 Buoy Buoy_old  ...  \
1  intercostal neuralgia        None  atypical chest pain     None  ...   
2        costochondritis        None                 None     None  ...   
3                   None        None                 None     None  ...   
4                   None        None                 None     None  ...   
5                   None        None                 None     None  ...   
6                   None        None                 None     None  ...   
7                   None        None                 None     None  ...   
8                   None        None                 None     None  ...   

                           Mediktor             Symptomate  \
1        musculoskeletal chest pain  intercostal neuralgia   
2                   costochondritis                   None   
3  primary spontaneous pneumothorax                   None   
4                       myocarditis                   None   
5                      pericarditis                   None   
6             myocardial infarction                   None   
7                              None                   None   
8                              None                   None   

                      WebMD                WebMD_old              doctor_MA  \
1              rib fracture              broken ribs  intercostal neuralgia   
2           costochondritis          costochondritis   inter coastal strain   
3                      gerd  gastroesophageal reflux                   None   
4        pulmonary embolism       pulmonary embolism                   None   
5              pericarditis       acute pericarditis                   None   
6               esophagitis              esophagitis                   None   
7  diffuse esophageal spasm                     None                   None   
8           unstable angina                     None                   None   

           doctor_MA_old              doctor_NJ          doctor_NJ_old  \
1  intercostal neuralgia         lung contusion         lung contusion   
2   inter coastal strain  intercostal neuralgia  intercostal neuralgia   
3                   None                   None                   None   
4                   None                   None                   None   
5                   None                   None                   None   
6                   None                   None                   None   
7                   None                   None                   None   
8                   None                   None                   None   

               doctor_TH          do




Case number 368 (common)
No diseases were found for: Babylon_old, Buoy_old.


gold                    gold_old  \
1     foreign body aspiration     foreign body aspiration   
2  central airway obstruction  central airway obstruction   
3                        None                        None   
4                        None                        None   
5                        None                        None   
6                        None                        None   
7                        None                        None   
8                        None                        None   

                                                 Ada  \
1                          acute respiratory failure   
2                                 pulmonary embolism   
3                            foreign body aspiration   
4  acute aspiration of oropharyngeal or gastric c...   
5                                      heart failure   
6                                               None   
7                                               None   
8                                               None   

                                             Ada_old  \
1                                             asthma   
2                            foreign body aspiration   
3                                 esophageal fistula   
4  acute aspiration of oropharyngeal or gastric c...   
5                           acute left heart failure   
6                                               None   
7                                               None   
8                                               None   

                                    Avey  \
1                foreign body aspiration   
2                              pneumonia   
3             central airway obstruction   
4  chronic obstructive pulmonary disease   
5                       acute bronchitis   
6                                   None   
7                                   None   
8                                   None   

                                 Avey v2                    Avey_old  \
1                foreign body aspiration     foreign body aspiration   
2                              pneumonia                      asthma   
3             central airway obstruction  central airway obstruction   
4  chronic obstructive pulmonary disease          pulmonary embolism   
5                       acute bronchitis             pulmonary edema   
6                                   None                        None   
7                                   None                        None   
8                                   None                        None   

  Babylon_old       Buoy Buoy_old  ...                     Mediktor  \
1        None  pneumonia     None  ...                       asthma   
2        None     asthma     None  ...             acute bronchitis   
3        None       None     None  ...            typical pneumonia   
4        None       None     None  ...      foreign body aspiration   
5        None       None     None  ...                heart failure   
6        None       None     None  ...  biventricular heart failure   
7        None       None     None  ...                     covid 19   
8        None       None     None  ...                 tuberculosis   

           Symptomate                     WebMD  \
1  pulmonary embolism                    asthma   
2                None          acute bronchitis   
3                None  congestive heart failure   
4                None             heart failure   
5                None                 emphysema   
6                None                 pneumonia   
7                None        pulmonary embolism   
8                None                 infuelnza   

                         WebMD_old                doctor_MA  \
1                           asthma  foreign body aspiration   
2                       bronchitis                     None   
3          foreign body aspiration                     None   
4         coronavirus disease 2019                     None   
5  s




Case number 500 (common)
Session failed to start for: Healthily, K Health, K health_old.
No diseases were found for: Babylon_old.


gold             gold_old                   Ada  \
1  tonsillopharyngitis  tonsillopharyngitis  bacterial tonsilitis   
2        mononucleosis        mononucleosis             influenza   
3            influenza            influenza   tonsillopharyngitis   
4                 None                 None              covid 19   
5                 None                 None                  None   
6                 None                 None                  None   
7                 None                 None                  None   
8                 None                 None                  None   

               Ada_old                 Avey              Avey v2  \
1  tonsillopharyngitis  tonsillopharyngitis  tonsillopharyngitis   
2          common cold           diphtheria           diphtheria   
3            influenza                croup                croup   
4                 None     acute laryngitis     acute laryngitis   
5                 None     acute bronchitis            influenza   
6                 None                 None                 None   
7                 None                 None                 None   
8                 None                 None                 None   

                   Avey_old Babylon_old                 Buoy  \
1       tonsillopharyngitis        None  tonsillopharyngitis   
2             lymphadenitis        None          common cold   
3               common cold        None     acute laryngitis   
4                 influenza        None                 None   
5  coronavirus disease 2019        None                 None   
6                laryngitis        None                 None   
7                      None        None                 None   
8                      None        None                 None   

               Buoy_old  ...          Mediktor           Symptomate  \
1  possible coronavirus  ...          covid 19  tonsillopharyngitis   
2                  None  ...     mononucleosis            influenza   
3                  None  ...         influenza     acute bronchitis   
4                  None  ...  acute bronchitis          pharyngitis   
5                  None  ...      tuberculosis     acute laryngitis   
6                  None  ...              None            pneumonia   
7                  None  ...              None         otitis media   
8                  None  ...              None                 None   

                  WebMD              WebMD_old            doctor_MA  \
1           common cold    tonsillopharyngitis            influenza   
2             hay fever  peritonsillar abscess  tonsillopharyngitis   
3  adenovirus infection            common cold                 None   
4              covid 19          mononucleosis                 None   
5     chronic sinusitis                   None                 None   
6       acute sinusitis                   None                 None   
7             influenza                   None                 None   
8      acute bronchitis                   None                 None   

         doctor_MA_old  doctor_NJ                            doctor_NJ_old  \
1          common cold  influenza  viral upper respiratory tract infection   
2  tonsillopharyngitis       None                                     None   
3                 None       None                                     None   
4                 None       None                                     None   
5                 None       None                                     None   
6                 None       None                                     None   
7                 None       None                                     None   
8                 None       None                                     None   

                  doctor_TH             doctor_TH_old  
1             mononucleosis             mononucleosis  
2       tonsillopharyngitis       tonsillopharyngitis  
3  coronavirus disease 2019  coronavirus disease 2019  

<p>

## Let us define the metrics now. <a class="anchor" id="metrics"></a>

### Terms used
- TP: True positive (correct disease retrieved)
- TN: True negative (wrong disease **not** retrieved)
- FP: False positive (wrong disease retrieved)
- FN: False negative (correct disease **not** retrieved)
- gold standard - the correct list of diseases as determined by collective intelligence of doctors

### Precision
Precision helps us understand how exact our results are. It gives us an intuition about how many wrong diseases (false positives) are being retrieved. It is the ratio *number of correct diseases retrieved* to the *length of the complete list retrieved*.
$$precision = \frac{TP}{TP + FP} = \frac{TP}{\text{length of differential list}}$$

### Recall
Recall is a measure of how many of the correct diseases are being retrieved. It is the ratio *number of correct diseases retrieved* to the *length of the gold standard list*.
$$recall = \frac{TP}{TP + FN} = \frac{TP}{\text{length of the gold standard}}$$

### F1 Score
F1 score is the weighted harmonic mean of *precision* and *recall*. It is a metric that combines *precision* and *recall* and gives us 1 score for easier comparison.

Suppose $\beta$ defines how important is $recall$ to $precision$ then,
$$fscore_{\beta} = (1 + \beta^2)\frac{precision \cdot recall}{(\beta^2 \cdot precision) + recall}$$
Substituting $\beta = 1$,
$$fscore_{1} = \frac{2 \cdot precision \cdot recall}{ precision + recall}$$

### NDCG
NDCG or Normalized Discounted Cumulative Gain is measure of how accurate the ranking is. In our calculations, we use
$$DCG = \sum_{i=1}^n\frac{2^{relevance_i}-1}{log_2(i+1)}$$
where $n$ is the number of differentials in the returned list and  
$relevance_i = |gold standard| - rank_{gold\ standard}(ddx[i])$ if $ddx[i]$ is present, 0 otherwise.

$$NDCG = \frac{DCG_{ddx}}{DCG_{gold\ standard}}$$

### M Score
M Score determines where the top disease (gold standard) appears in the returned differential.
$$M_i = \text{gold standard[0]} \in \text{ddx[:i]}$$

### Position
Shows the position of the gold standard[0] in the returned differential. 

### Length
$$length = \frac{|ddx|}{|gold\ standard|}$$
<br>
<br>
<br>
<br>


In [7]:
import math

def getPrecision(goldStandard: pd.Series, candidate: pd.Series) -> float:
    tp = sum(int(disease in goldStandard.values and disease is not None)
             for disease in candidate)
    return tp if tp == 0 else tp/candidate.count()


def getRecall(goldStandard: pd.Series, candidate: pd.Series) -> float:
    tp = sum(int(disease in goldStandard.values and disease is not None)
             for disease in candidate)
    return tp/goldStandard.count()


def getFScore(precision: float, recall: float, beta: float = 1) -> float:
    return math.nan if precision+recall == 0 else \
        (1+beta**2)*precision*recall/(precision*(beta**2)+recall)


def getNDCG(goldStandard: pd.Series, candidate: pd.Series, scores) -> float:
    def discount(score: float, index: int) -> float:
        '''The index is 1 based'''
        return (math.pow(2, score)-1)/math.log2(index+1)

    maxDCG = sum(discount(scores[i], i+1) for i in range(len(scores)))

    candidateRelevance = []
    goldStandard = list(goldStandard)
    for index, disease in enumerate(candidate):
        if disease is not None and disease in goldStandard:
            candidateRelevance.append(
                discount(scores[goldStandard.index(disease)], index+1))
        else:
            candidateRelevance.append(0)

    return sum(candidateRelevance)/maxDCG


def getMScore(goldStandard: pd.Series, candidate: pd.Series, m=1) -> bool:
    return goldStandard.values[0] in candidate.values[:m]


def getPosition(goldStandard: pd.Series, candidate: pd.Series) -> bool:
    return math.nan if goldStandard.values[0] not in candidate.values else\
        1 + list(candidate.values).index(goldStandard.values[0])


def getLength(goldStandard: pd.Series, candidate: pd.Series) -> int:
    return math.nan if candidate.count() == 0 else \
        candidate.count()/goldStandard.count()


def getScoresCase(id,case: pd.DataFrame) -> pd.DataFrame:
    gold = case['gold']
    if EXPERIMENT_TAG == 'avey':
        gold_old = case['gold_old']
    else:
        gold_old = gold

    scores = [
        [getPrecision(gold_old if '_old' in col else gold, case[col]) for col in case.columns if "gold" not in col],
        [getRecall(gold_old if '_old' in col else gold, case[col]) for col in case.columns if "gold" not in col],
    ]

    scores.append(
        [getFScore(prec, rec, beta=1) for prec, rec in zip(scores[0], scores[1])]
    )
    scores.append(
        [getFScore(prec, rec, beta=2) for prec, rec in zip(scores[0], scores[1])]
    )

    # relevance for a list of 4 is 4, 3, 2, 1
    # relevance for a list of 2 is 2, 1
    scores.append(
        [
            getNDCG(
                gold_old if "_old" in col else gold,
                case[col],
                list(range((gold_old if "_old" in col else gold).count(), 0, -1)),
            )
            for col in case.columns
            if "gold" not in col
        ]
    )

    for m in range(1, 6, 2):
        scores.append(
            [
                getMScore(gold_old if "_old" in col else gold, case[col], m)
                for col in case.columns
                if "gold" not in col
            ]
        )

    try:
        scores.append(
            [
                getPosition(gold_old if "_old" in col else gold, case[col])
                for col in case.columns
                if "gold" not in col
            ]
        )
    except Exception as e:
        print(id,flush=True)
        raise e

    scores.append(
        [
            getLength(gold_old if "_old" in col else gold, case[col])
            for col in case.columns
            if "gold" not in col
        ]
    )

    return pd.DataFrame(
        scores,
        columns=[col for col in case.columns if "gold" not in col],
        index=[
            "precision",
            "recall",
            "f1-score",
            "f2-score",
            "NDCG",
            "M1",
            "M3",
            "M5",
            "position",
            "length (x of gs)",
        ],
    )

scores = {}
for id, case in cases.items():
    try: scores[id] = getScoresCase(id, case)
    except Exception as e:
        print(id,flush=True)
        raise e

# scores = {id: getScoresCase(id, case) for id, case in cases.items()}

In [8]:
for id, score in scores.items():
    score.to_excel(f'individual_results/{EXPERIMENT_TAG}/{id}.xlsx')

In [9]:
print(len(scores))

485


Let us define the experiment now. We will pick which cases to compute startistics for.

In [10]:
from enum import Enum 

class DiseaseType(Enum):
    ALL = 'all'
    COMMON = 'common-diseases'
    UNCOMMON = 'less-common-diseases'

class FailureType(Enum):
    ANY = 'any-error'
    NO_DDX = 'no-disease-found'
    SES_FAIL = 'session-failed'
    NONE = 'None'

In [11]:
from collections import defaultdict

experiments = {}

def getExpName(disease_type:DiseaseType,failure_type:FailureType=FailureType.NONE,app='NA'):
    return f"disease_type={disease_type.value} failure-type-ignored={failure_type.value} for app={app}"

def addExperiment(disease_type, casesToConsider):
    # add experiment to ignore no case
    experiments[getExpName(disease_type)] = set(casesToConsider)

    caseClassificationApps = {}
    for app, failure_type in caseClassification["apps"].items():
        caseClassificationApps[app] = {
            FailureType.NO_DDX: failure_type["no disease found"],
            FailureType.SES_FAIL: failure_type["session failed"],
            FailureType.ANY: set(failure_type["no disease found"])
            | set(failure_type["session failed"]),
        }

    for app, classifications in caseClassificationApps.items():
        for failure_type, caseNums in classifications.items():

            # experiment to ignore the cases for the particular app
            experiments[getExpName(disease_type,failure_type,app)] = set(casesToConsider) - set(caseNums)

            # experiment to ignore the cases for all the apps
            if getExpName(disease_type,failure_type,'any') in experiments:
                experiments[getExpName(disease_type,failure_type,'any')] = (
                    experiments[getExpName(disease_type,failure_type,'any')]
                    - set(caseNums)
                )
            else:
                experiments[getExpName(disease_type,failure_type,'any')] = experiments[getExpName(disease_type,failure_type,app)]


addExperiment(DiseaseType.COMMON, caseClassification["common"])
addExperiment(DiseaseType.UNCOMMON, caseClassification["less common"])
addExperiment(
    DiseaseType.ALL,
    set(caseClassification["less common"]) | set(caseClassification["common"]),
)

display("The experiments we are going to conduct are:")
dict(enumerate(sorted(list(experiments.keys()))))

'The experiments we are going to conduct are:'

{0: 'disease_type=all failure-type-ignored=None for app=NA',
 1: 'disease_type=all failure-type-ignored=any-error for app=Ada_old',
 2: 'disease_type=all failure-type-ignored=any-error for app=Avey',
 3: 'disease_type=all failure-type-ignored=any-error for app=Avey v2',
 4: 'disease_type=all failure-type-ignored=any-error for app=Avey_old',
 5: 'disease_type=all failure-type-ignored=any-error for app=Babylon_old',
 6: 'disease_type=all failure-type-ignored=any-error for app=Buoy',
 7: 'disease_type=all failure-type-ignored=any-error for app=Buoy_old',
 8: 'disease_type=all failure-type-ignored=any-error for app=Healthily',
 9: 'disease_type=all failure-type-ignored=any-error for app=K Health',
 10: 'disease_type=all failure-type-ignored=any-error for app=K health_old',
 11: 'disease_type=all failure-type-ignored=any-error for app=Mediktor',
 12: 'disease_type=all failure-type-ignored=any-error for app=Symptomate',
 13: 'disease_type=all failure-type-ignored=any-error for app=WebMD',
 1

<br>
<br>

### Results <a class="anchor" id="results"></a>

In [15]:
# shows the number of cases where Avey failed M1
# Do not run this after Avey v2 is replaces Avey

count = 0
for id, score in scores.items():
    if not score.loc["M1", "Avey v2"]:
        print(id)
        count += 1 

count/len(scores)

21
22
24
26
43
65
75
118
149
159
182
187
206
207
225
229
233
246
251
261
266
271
290
299
300
308
311
326
336
344
354
359
366
393
411
414
416
420
423
438
444
445
461
472
474
489
490
491
493
499
5
30
31
34
38
40
44
57
146
154
164
209
211
217
219
224
236
248
252
254
285
292
301
305
310
312
325
339
351
356
388
404
409
425
437
446
462
464
9
10
12
36
50
55
62
78
79
80
90
94
101
102
106
109
113
116
120
124
126
141
143
155
158
162
163
172
173
176
181
185
188
198
214
226
241
249
257
258
268
276
279
281
288
296
303
304
306
313
321
323
331
337
346
349
353
357
375
384
395
400
410
412
424
428
429
431
434
436
439
440
441
442
448
453
455
458
467
473
475
478
483
488
496
66
71
160
195
216
275
309
335
343
362
378
430
486
494
17
133


0.38969072164948454

In [96]:
def getStats(scores, row: str, col: str):
    values = []
    for score in scores.values():
        try:
            if not math.isnan(score.loc[row, col]):
                values.append(score.loc[row, col])
        except KeyError as e:
            if '_old' not in col:
                display(score,row,col)
                raise e
    if not values:
        return {
            (col, "average"): 0,
            (col, "variance"): 0,
            (col, "std Dev"): 0,
        }
    
    average = sum(values)/len(values)
    variance = sum((value-average)**2 for value in values)/len(values)
    stdDev = variance**0.5
    return {
        (col,"average"): round(average, 3), 
        (col,"variance"):round(variance, 3), 
        (col,"std Dev"):round(stdDev, 3),
        }


results = {}
for label, casesToConsider in experiments.items():
    # selectedScores = {id: score for id,
    #                   score in scores.items()}
    selectedScores = {id: score for id,
                      score in scores.items() if int(id) in casesToConsider}
    
    columns = next(iter(scores.values())).columns
    index = [
            "precision",
            "recall",
            "f1-score",
            "f2-score",
            "NDCG",
            "M1",
            "M3",
            "M5",
            "position",
            "length (x of gs)",
    ]

    metrics = defaultdict(list)
    for row in index:
        for stat in [getStats(selectedScores, row, col) for col in columns]:
            for key,val in stat.items():
                metrics[key].append(val)

    averageScores = pd.DataFrame(metrics, index=[f"stats_for_{x}" for x in index])

    # ignore nan for recall
    for col in columns:
        p = averageScores.loc["stats_for_precision", (col,'average')]
        r = averageScores.loc["stats_for_recall", (col, "average")]
        averageScores.loc["stats_for_f1-score", (col, "average")] = round(getFScore(p, r, 1), 3)
        averageScores.loc["stats_for_f2-score", (col, "average")] = round(getFScore(p, r, 2), 3)

        for key in ['variance','std Dev']:
            averageScores.loc["stats_for_f1-score", (col, key)] = np.nan
            averageScores.loc["stats_for_f2-score", (col, key)] = np.nan

    def calcStats(doctorResults):
        def extractItem(data, col='average'):
            return data[col].copy()

        sum = pd.Series(extractItem(doctorResults[0]))
        for data in doctorResults[1:]:
            sum += extractItem(data)
        average = (sum/len(doctorResults)).round(3)
        return average

    doctorResultsAverage = calcStats(
        [
            averageScores.loc[:, "doctor_MA"] ,
            averageScores.loc[:, "doctor_NJ"] ,
            averageScores.loc[:, "doctor_TH"]
        ]
    )

    if EXPERIMENT_TAG != 'harvard':
        doctorResultsAverageOld = calcStats(
            [
                averageScores.loc[:, "doctor_MA_old"] ,
                averageScores.loc[:, "doctor_NJ_old"] ,
                averageScores.loc[:, "doctor_TH_old"]
            ]
        )
        averageScores["average_doctor_old"] = doctorResultsAverageOld

    # averageScores.insert(
    #     loc=8, column="average_doctor",
    #     value=doctorResultsAverage,
    # )

    averageScores["average_doctor"] = doctorResultsAverage

    results[label] = averageScores

In [97]:
def displayResults(results,printNumCases=True):
    for label, result in results.items():
        if printNumCases:
            print(f'Results for experiment `{label}`, which has {len(set(experiments[label]) & set(scores.keys()))} cases, is')
        else:
            print(f'Results for experiment `{label}` is')
        display(result)
        result.to_excel(f'stats/{EXPERIMENT_TAG}/{label}.xlsx')

displayResults({key:val for key, val in results.items()})

Results for experiment `disease_type=common-diseases failure-type-ignored=None for app=NA`, which has 267 cases, is


Ada                  Ada_old                   \
                           average variance std Dev average variance std Dev   
stats_for_precision          0.436    0.064   0.254   0.489    0.063   0.251   
stats_for_recall             0.537    0.079   0.280   0.640    0.070   0.265   
stats_for_f1-score           0.481      NaN     NaN   0.554      NaN     NaN   
stats_for_f2-score           0.513      NaN     NaN   0.603      NaN     NaN   
stats_for_NDCG               0.614    0.096   0.309   0.721    0.069   0.263   
stats_for_M1                 0.524    0.249   0.499   0.645    0.229   0.478   
stats_for_M3                 0.742    0.192   0.438   0.834    0.138   0.372   
stats_for_M5                 0.783    0.170   0.412   0.876    0.109   0.330   
stats_for_position           1.522    0.795   0.892   1.437    0.772   0.879   
stats_for_length (x of gs)   1.377    0.319   0.565   1.500    0.360   0.600   

                              Avey                  Avey v2  ...  \
                           average variance std Dev average  ...   
stats_for_precision          0.414    0.063   0.250   0.418  ...   
stats_for_recall             0.646    0.111   0.333   0.665  ...   
stats_for_f1-score           0.505      NaN     NaN   0.513  ...   
stats_for_f2-score           0.581      NaN     NaN   0.595  ...   
stats_for_NDCG               0.689    0.106   0.326   0.730  ...   
stats_for_M1                 0.599    0.240   0.490   0.678  ...   
stats_for_M3                 0.787    0.168   0.410   0.839  ...   
stats_for_M5                 0.824    0.145   0.381   0.873  ...   
stats_for_position           1.386    0.573   0.757   1.369  ...   
stats_for_length (x of gs)   1.751    0.491   0.700   1.753  ...   

                           doctor_NJ_old         doctor_TH                   \
                                variance std Dev   average variance std Dev   
stats_for_precision                0.116   0.341     0.781    0.068   0.261   
stats_for_recall                   0.045   0.211     0.550    0.053   0.229   
stats_for_f1-score                   NaN     NaN     0.645      NaN     NaN   
stats_for_f2-score                   NaN     NaN     0.585      NaN     NaN   
stats_for_NDCG                     0.092   0.304     0.743    0.046   0.213   
stats_for_M1                       0.223   0.472     0.760    0.182   0.427   
stats_for_M3                       0.200   0.447     0.903    0.088   0.296   
stats_for_M5                       0.200   0.447     0.906    0.085   0.291   
stats_for_position                 0.130   0.360     1.182    0.198   0.445   
stats_for_length (x of gs)         0.093   0.306     0.797    0.183   0.428   

                           doctor_TH_old                  average_doctor_old  \
                                 average variance std Dev                      
stats_for_precision                0.742    0.077   0.278              0.720   
stats_for_recall                   0.562    0.057   0.239              0.469   
stats_for_f1-score                 0.640      NaN     NaN              0.564   
stats_for_f2-score                 0.591      NaN     NaN              0.503   
stats_for_NDCG                     0.736    0.056   0.236              0.642   
stats_for_M1                       0.747    0.189   0.435              0.659   
stats_for_M3                       0.880    0.105   0.325              0.771   
stats_for_M5                       0.885    0.102   0.319              0.774   
stats_for_position                 1.182    0.212   0.460              1.176   
stats_for_length (x of gs)         0.860    0.206   0.453              0.764   

                           average_doctor  
                                           
stats_for_precision                 0.746  
stats_for_recall                    0.467  
stats_for_f1-score                  0.571  
stats_for_f2-score                  0.503  
stats_for_NDCG                      0.656  
stats_for_M1                       

Results for experiment `disease_type=common-diseases failure-type-ignored=no-disease-found for app=Avey`, which has 261 cases, is


Ada                  Ada_old                   \
                           average variance std Dev average variance std Dev   
stats_for_precision          0.440    0.064   0.253   0.494    0.064   0.252   
stats_for_recall             0.540    0.078   0.279   0.639    0.069   0.263   
stats_for_f1-score           0.485      NaN     NaN   0.557      NaN     NaN   
stats_for_f2-score           0.517      NaN     NaN   0.604      NaN     NaN   
stats_for_NDCG               0.620    0.094   0.307   0.718    0.069   0.264   
stats_for_M1                 0.536    0.249   0.499   0.640    0.230   0.480   
stats_for_M3                 0.751    0.187   0.432   0.829    0.142   0.376   
stats_for_M5                 0.793    0.164   0.405   0.872    0.112   0.334   
stats_for_position           1.517    0.800   0.895   1.446    0.791   0.889   
stats_for_length (x of gs)   1.365    0.310   0.557   1.487    0.352   0.594   

                              Avey                  Avey v2  ...  \
                           average variance std Dev average  ...   
stats_for_precision          0.424    0.060   0.245   0.423  ...   
stats_for_recall             0.661    0.104   0.322   0.672  ...   
stats_for_f1-score           0.517      NaN     NaN   0.519  ...   
stats_for_f2-score           0.595      NaN     NaN   0.601  ...   
stats_for_NDCG               0.705    0.097   0.312   0.739  ...   
stats_for_M1                 0.613    0.237   0.487   0.690  ...   
stats_for_M3                 0.805    0.157   0.397   0.851  ...   
stats_for_M5                 0.843    0.132   0.364   0.885  ...   
stats_for_position           1.386    0.573   0.757   1.368  ...   
stats_for_length (x of gs)   1.751    0.491   0.700   1.753  ...   

                           doctor_NJ_old         doctor_TH                   \
                                variance std Dev   average variance std Dev   
stats_for_precision                0.118   0.343     0.780    0.068   0.260   
stats_for_recall                   0.042   0.205     0.549    0.052   0.227   
stats_for_f1-score                   NaN     NaN     0.644      NaN     NaN   
stats_for_f2-score                   NaN     NaN     0.584      NaN     NaN   
stats_for_NDCG                     0.093   0.304     0.744    0.045   0.211   
stats_for_M1                       0.223   0.473     0.762    0.181   0.426   
stats_for_M3                       0.201   0.449     0.904    0.087   0.294   
stats_for_M5                       0.201   0.449     0.908    0.083   0.289   
stats_for_position                 0.110   0.332     1.181    0.199   0.446   
stats_for_length (x of gs)         0.092   0.303     0.797    0.186   0.432   

                           doctor_TH_old                  average_doctor_old  \
                                 average variance std Dev                      
stats_for_precision                0.741    0.077   0.277              0.720   
stats_for_recall                   0.561    0.056   0.237              0.466   
stats_for_f1-score                 0.639      NaN     NaN              0.562   
stats_for_f2-score                 0.590      NaN     NaN              0.500   
stats_for_NDCG                     0.736    0.055   0.235              0.639   
stats_for_M1                       0.749    0.188   0.434              0.657   
stats_for_M3                       0.882    0.104   0.323              0.769   
stats_for_M5                       0.886    0.101   0.318              0.772   
stats_for_position                 1.182    0.213   0.461              1.176   
stats_for_length (x of gs)         0.863    0.210   0.458              0.760   

                           average_doctor  
                                           
stats_for_precision                 0.747  
stats_for_recall                    0.464  
stats_for_f1-score                  0.568  
stats_for_f2-score                  0.500  
stats_for_NDCG                      0.654  
stats_for_M1                       

Results for experiment `disease_type=common-diseases failure-type-ignored=no-disease-found for app=any`, which has 59 cases, is


...

Ada                  Ada_old                   \
                           average variance std Dev average variance std Dev   
stats_for_precision          0.403    0.078   0.280   0.447    0.073   0.271   
stats_for_recall             0.500    0.092   0.303   0.589    0.089   0.298   
stats_for_f1-score           0.446      NaN     NaN   0.508      NaN     NaN   
stats_for_f2-score           0.477      NaN     NaN   0.554      NaN     NaN   
stats_for_NDCG               0.544    0.115   0.339   0.634    0.105   0.324   
stats_for_M1                 0.440    0.246   0.496   0.539    0.248   0.498   
stats_for_M3                 0.639    0.231   0.480   0.715    0.204   0.452   
stats_for_M5                 0.687    0.215   0.464   0.764    0.180   0.424   
stats_for_position           1.604    0.976   0.988   1.521    0.955   0.977   
stats_for_length (x of gs)   1.451    0.349   0.591   1.575    0.463   0.681   

                              Avey                  Avey v2  ...  \
                           average variance std Dev average  ...   
stats_for_precision          0.383    0.067   0.259   0.396  ...   
stats_for_recall             0.596    0.125   0.353   0.629  ...   
stats_for_f1-score           0.466      NaN     NaN   0.486  ...   
stats_for_f2-score           0.536      NaN     NaN   0.563  ...   
stats_for_NDCG               0.623    0.126   0.356   0.676  ...   
stats_for_M1                 0.527    0.249   0.499   0.610  ...   
stats_for_M3                 0.714    0.204   0.452   0.774  ...   
stats_for_M5                 0.759    0.183   0.427   0.805  ...   
stats_for_position           1.500    0.867   0.931   1.384  ...   
stats_for_length (x of gs)   1.774    0.463   0.681   1.778  ...   

                           doctor_NJ_old         doctor_TH                   \
                                variance std Dev   average variance std Dev   
stats_for_precision                0.123   0.350     0.753    0.078   0.278   
stats_for_recall                   0.049   0.222     0.559    0.059   0.242   
stats_for_f1-score                   NaN     NaN     0.642      NaN     NaN   
stats_for_f2-score                   NaN     NaN     0.589      NaN     NaN   
stats_for_NDCG                     0.099   0.314     0.733    0.052   0.227   
stats_for_M1                       0.237   0.487     0.728    0.198   0.445   
stats_for_M3                       0.218   0.467     0.890    0.098   0.313   
stats_for_M5                       0.217   0.466     0.892    0.096   0.310   
stats_for_position                 0.169   0.412     1.232    0.303   0.551   
stats_for_length (x of gs)         0.094   0.306     0.845    0.197   0.444   

                           doctor_TH_old                  average_doctor_old  \
                                 average variance std Dev                      
stats_for_precision                0.720    0.086   0.293              0.695   
stats_for_recall                   0.574    0.067   0.259              0.466   
stats_for_f1-score                 0.639      NaN     NaN              0.554   
stats_for_f2-score                 0.598      NaN     NaN              0.497   
stats_for_NDCG                     0.733    0.059   0.243              0.612   
stats_for_M1                       0.720    0.202   0.449              0.612   
stats_for_M3                       0.882    0.104   0.322              0.726   
stats_for_M5                       0.885    0.102   0.319              0.730   
stats_for_position                 1.242    0.331   0.575              1.204   
stats_for_length (x of gs)         0.913    0.241   0.491              0.790   

                           average_doctor  
                                           
stats_for_precision                 0.711  
stats_for_recall                    0.457  
stats_for_f1-score                  0.553  
stats_for_f2-score                  0.490  
stats_for_NDCG                      0.614  
stats_for_M1                       

Results for experiment `disease_type=all failure-type-ignored=session-failed for app=WebMD_old`, which has 482 cases, is


Ada                  Ada_old                   \
                           average variance std Dev average variance std Dev   
stats_for_precision          0.402    0.078   0.279   0.447    0.073   0.270   
stats_for_recall             0.502    0.092   0.303   0.591    0.088   0.297   
stats_for_f1-score           0.446      NaN     NaN   0.509      NaN     NaN   
stats_for_f2-score           0.478      NaN     NaN   0.555      NaN     NaN   
stats_for_NDCG               0.545    0.115   0.339   0.637    0.104   0.323   
stats_for_M1                 0.442    0.247   0.497   0.542    0.248   0.498   
stats_for_M3                 0.639    0.231   0.480   0.717    0.203   0.450   
stats_for_M5                 0.687    0.215   0.464   0.767    0.179   0.423   
stats_for_position           1.598    0.971   0.986   1.519    0.953   0.976   
stats_for_length (x of gs)   1.457    0.353   0.594   1.579    0.463   0.681   

                              Avey                  Avey v2  ...  \
                           average variance std Dev average  ...   
stats_for_precision          0.381    0.067   0.258   0.395  ...   
stats_for_recall             0.595    0.126   0.354   0.629  ...   
stats_for_f1-score           0.465      NaN     NaN   0.485  ...   
stats_for_f2-score           0.535      NaN     NaN   0.562  ...   
stats_for_NDCG               0.623    0.127   0.356   0.678  ...   
stats_for_M1                 0.529    0.249   0.499   0.614  ...   
stats_for_M3                 0.714    0.204   0.452   0.776  ...   
stats_for_M5                 0.759    0.183   0.427   0.807  ...   
stats_for_position           1.497    0.867   0.931   1.380  ...   
stats_for_length (x of gs)   1.776    0.462   0.680   1.780  ...   

                           doctor_NJ_old         doctor_TH                   \
                                variance std Dev   average variance std Dev   
stats_for_precision                0.124   0.352     0.751    0.078   0.278   
stats_for_recall                   0.049   0.222     0.559    0.059   0.242   
stats_for_f1-score                   NaN     NaN     0.641      NaN     NaN   
stats_for_f2-score                   NaN     NaN     0.589      NaN     NaN   
stats_for_NDCG                     0.099   0.315     0.734    0.051   0.227   
stats_for_M1                       0.237   0.487     0.730    0.197   0.444   
stats_for_M3                       0.219   0.468     0.892    0.096   0.310   
stats_for_M5                       0.218   0.467     0.894    0.095   0.308   
stats_for_position                 0.170   0.412     1.231    0.303   0.550   
stats_for_length (x of gs)         0.094   0.306     0.847    0.197   0.444   

                           doctor_TH_old                  average_doctor_old  \
                                 average variance std Dev                      
stats_for_precision                0.717    0.085   0.292              0.693   
stats_for_recall                   0.574    0.067   0.259              0.466   
stats_for_f1-score                 0.638      NaN     NaN              0.553   
stats_for_f2-score                 0.598      NaN     NaN              0.497   
stats_for_NDCG                     0.734    0.059   0.242              0.612   
stats_for_M1                       0.723    0.200   0.448              0.612   
stats_for_M3                       0.885    0.102   0.319              0.726   
stats_for_M5                       0.887    0.100   0.316              0.729   
stats_for_position                 1.241    0.330   0.575              1.204   
stats_for_length (x of gs)         0.916    0.239   0.489              0.791   

                           average_doctor  
                                           
stats_for_precision                 0.710  
stats_for_recall                    0.457  
stats_for_f1-score                  0.553  
stats_for_f2-score                  0.490  
stats_for_NDCG                      0.614  
stats_for_M1                       

Results for experiment `disease_type=all failure-type-ignored=any-error for app=WebMD_old`, which has 479 cases, is


Ada                  Ada_old                   \
                           average variance std Dev average variance std Dev   
stats_for_precision          0.403    0.078   0.280   0.448    0.073   0.271   
stats_for_recall             0.501    0.092   0.303   0.590    0.088   0.297   
stats_for_f1-score           0.447      NaN     NaN   0.509      NaN     NaN   
stats_for_f2-score           0.478      NaN     NaN   0.555      NaN     NaN   
stats_for_NDCG               0.545    0.115   0.339   0.635    0.105   0.323   
stats_for_M1                 0.443    0.247   0.497   0.538    0.249   0.499   
stats_for_M3                 0.639    0.231   0.480   0.715    0.204   0.451   
stats_for_M5                 0.687    0.215   0.464   0.765    0.180   0.424   
stats_for_position           1.599    0.976   0.988   1.524    0.960   0.980   
stats_for_length (x of gs)   1.450    0.348   0.590   1.577    0.465   0.682   

                              Avey                  Avey v2  ...  \
                           average variance std Dev average  ...   
stats_for_precision          0.383    0.067   0.258   0.396  ...   
stats_for_recall             0.597    0.125   0.353   0.630  ...   
stats_for_f1-score           0.467      NaN     NaN   0.486  ...   
stats_for_f2-score           0.537      NaN     NaN   0.563  ...   
stats_for_NDCG               0.625    0.126   0.355   0.678  ...   
stats_for_M1                 0.530    0.249   0.499   0.614  ...   
stats_for_M3                 0.716    0.203   0.451   0.777  ...   
stats_for_M5                 0.762    0.181   0.426   0.808  ...   
stats_for_position           1.499    0.869   0.932   1.382  ...   
stats_for_length (x of gs)   1.774    0.463   0.680   1.778  ...   

                           doctor_NJ_old         doctor_TH                   \
                                variance std Dev   average variance std Dev   
stats_for_precision                0.123   0.351     0.752    0.078   0.279   
stats_for_recall                   0.049   0.222     0.559    0.059   0.243   
stats_for_f1-score                   NaN     NaN     0.641      NaN     NaN   
stats_for_f2-score                   NaN     NaN     0.589      NaN     NaN   
stats_for_NDCG                     0.099   0.315     0.733    0.052   0.227   
stats_for_M1                       0.237   0.487     0.729    0.198   0.445   
stats_for_M3                       0.219   0.468     0.891    0.097   0.311   
stats_for_M5                       0.218   0.467     0.894    0.095   0.308   
stats_for_position                 0.171   0.414     1.233    0.305   0.552   
stats_for_length (x of gs)         0.094   0.307     0.848    0.198   0.445   

                           doctor_TH_old                  average_doctor_old  \
                                 average variance std Dev                      
stats_for_precision                0.717    0.086   0.293              0.692   
stats_for_recall                   0.575    0.067   0.260              0.466   
stats_for_f1-score                 0.638      NaN     NaN              0.553   
stats_for_f2-score                 0.599      NaN     NaN              0.497   
stats_for_NDCG                     0.734    0.059   0.243              0.611   
stats_for_M1                       0.720    0.201   0.449              0.609   
stats_for_M3                       0.884    0.103   0.320              0.725   
stats_for_M5                       0.887    0.101   0.317              0.728   
stats_for_position                 1.243    0.332   0.577              1.206   
stats_for_length (x of gs)         0.917    0.241   0.491              0.793   

                           average_doctor  
                                           
stats_for_precision                 0.710  
stats_for_recall                    0.457  
stats_for_f1-score                  0.552  
stats_for_f2-score                  0.490  
stats_for_NDCG                      0.613  
stats_for_M1                       

Now let us combine the individual results of the apps. We take the app results from different experiments and combine them. Our goal is to get the best results for each app and compare them.

In [98]:
bestResults = defaultdict(lambda : list(results.values())[0].copy())

for app in caseClassification['apps']:
    try:
        bestResults[getExpName(DiseaseType.ALL, FailureType.ANY, "best")][app] = results[
            getExpName(DiseaseType.ALL, FailureType.ANY, app)][app]
        bestResults[getExpName(DiseaseType.ALL, FailureType.SES_FAIL, "best")][app] = results[
            getExpName(DiseaseType.ALL, FailureType.ANY, app)][app]
        bestResults[getExpName(DiseaseType.ALL, FailureType.NO_DDX, "best")][app] = results[
            getExpName(DiseaseType.ALL, FailureType.ANY, app)][app]
    except Exception as e:
        display(getExpName(DiseaseType.ALL, FailureType.ANY, app))
        display(results[getExpName(DiseaseType.ALL, FailureType.ANY, app)])
        raise e

In [99]:
displayResults(bestResults,printNumCases=False)

Results for experiment `disease_type=all failure-type-ignored=any-error for app=best` is


Ada                  Ada_old                   \
                           average variance std Dev average variance std Dev   
stats_for_precision          0.436    0.064   0.254   0.446    0.073   0.270   
stats_for_recall             0.537    0.079   0.280   0.589    0.088   0.297   
stats_for_f1-score           0.481      NaN     NaN   0.508      NaN     NaN   
stats_for_f2-score           0.513      NaN     NaN   0.554      NaN     NaN   
stats_for_NDCG               0.614    0.096   0.309   0.636    0.105   0.324   
stats_for_M1                 0.524    0.249   0.499   0.543    0.248   0.498   
stats_for_M3                 0.742    0.192   0.438   0.717    0.203   0.451   
stats_for_M5                 0.783    0.170   0.412   0.766    0.179   0.423   
stats_for_position           1.522    0.795   0.892   1.515    0.948   0.974   
stats_for_length (x of gs)   1.377    0.319   0.565   1.577    0.462   0.680   

                              Avey                  Avey v2  ...  \
                           average variance std Dev average  ...   
stats_for_precision          0.403    0.063   0.250   0.405  ...   
stats_for_recall             0.628    0.112   0.334   0.643  ...   
stats_for_f1-score           0.491      NaN     NaN   0.497  ...   
stats_for_f2-score           0.565      NaN     NaN   0.575  ...   
stats_for_NDCG               0.657    0.112   0.334   0.691  ...   
stats_for_M1                 0.556    0.247   0.497   0.624  ...   
stats_for_M3                 0.752    0.187   0.432   0.791  ...   
stats_for_M5                 0.800    0.160   0.400   0.823  ...   
stats_for_position           1.499    0.866   0.930   1.382  ...   
stats_for_length (x of gs)   1.776    0.463   0.680   1.780  ...   

                           doctor_NJ_old         doctor_TH                   \
                                variance std Dev   average variance std Dev   
stats_for_precision                0.116   0.341     0.781    0.068   0.261   
stats_for_recall                   0.045   0.211     0.550    0.053   0.229   
stats_for_f1-score                   NaN     NaN     0.645      NaN     NaN   
stats_for_f2-score                   NaN     NaN     0.585      NaN     NaN   
stats_for_NDCG                     0.092   0.304     0.743    0.046   0.213   
stats_for_M1                       0.223   0.472     0.760    0.182   0.427   
stats_for_M3                       0.200   0.447     0.903    0.088   0.296   
stats_for_M5                       0.200   0.447     0.906    0.085   0.291   
stats_for_position                 0.130   0.360     1.182    0.198   0.445   
stats_for_length (x of gs)         0.093   0.306     0.797    0.183   0.428   

                           doctor_TH_old                  average_doctor_old  \
                                 average variance std Dev                      
stats_for_precision                0.742    0.077   0.278              0.720   
stats_for_recall                   0.562    0.057   0.239              0.469   
stats_for_f1-score                 0.640      NaN     NaN              0.564   
stats_for_f2-score                 0.591      NaN     NaN              0.503   
stats_for_NDCG                     0.736    0.056   0.236              0.642   
stats_for_M1                       0.747    0.189   0.435              0.659   
stats_for_M3                       0.880    0.105   0.325              0.771   
stats_for_M5                       0.885    0.102   0.319              0.774   
stats_for_position                 1.182    0.212   0.460              1.176   
stats_for_length (x of gs)         0.860    0.206   0.453              0.764   

                           average_doctor  
                                           
stats_for_precision                 0.746  
stats_for_recall                    0.467  
stats_for_f1-score                  0.571  
stats_for_f2-score                  0.503  
stats_for_NDCG                      0.656  
stats_for_M1                       

Results for experiment `disease_type=all failure-type-ignored=session-failed for app=best` is


Ada                  Ada_old                   \
                           average variance std Dev average variance std Dev   
stats_for_precision          0.436    0.064   0.254   0.446    0.073   0.270   
stats_for_recall             0.537    0.079   0.280   0.589    0.088   0.297   
stats_for_f1-score           0.481      NaN     NaN   0.508      NaN     NaN   
stats_for_f2-score           0.513      NaN     NaN   0.554      NaN     NaN   
stats_for_NDCG               0.614    0.096   0.309   0.636    0.105   0.324   
stats_for_M1                 0.524    0.249   0.499   0.543    0.248   0.498   
stats_for_M3                 0.742    0.192   0.438   0.717    0.203   0.451   
stats_for_M5                 0.783    0.170   0.412   0.766    0.179   0.423   
stats_for_position           1.522    0.795   0.892   1.515    0.948   0.974   
stats_for_length (x of gs)   1.377    0.319   0.565   1.577    0.462   0.680   

                              Avey                  Avey v2  ...  \
                           average variance std Dev average  ...   
stats_for_precision          0.403    0.063   0.250   0.405  ...   
stats_for_recall             0.628    0.112   0.334   0.643  ...   
stats_for_f1-score           0.491      NaN     NaN   0.497  ...   
stats_for_f2-score           0.565      NaN     NaN   0.575  ...   
stats_for_NDCG               0.657    0.112   0.334   0.691  ...   
stats_for_M1                 0.556    0.247   0.497   0.624  ...   
stats_for_M3                 0.752    0.187   0.432   0.791  ...   
stats_for_M5                 0.800    0.160   0.400   0.823  ...   
stats_for_position           1.499    0.866   0.930   1.382  ...   
stats_for_length (x of gs)   1.776    0.463   0.680   1.780  ...   

                           doctor_NJ_old         doctor_TH                   \
                                variance std Dev   average variance std Dev   
stats_for_precision                0.116   0.341     0.781    0.068   0.261   
stats_for_recall                   0.045   0.211     0.550    0.053   0.229   
stats_for_f1-score                   NaN     NaN     0.645      NaN     NaN   
stats_for_f2-score                   NaN     NaN     0.585      NaN     NaN   
stats_for_NDCG                     0.092   0.304     0.743    0.046   0.213   
stats_for_M1                       0.223   0.472     0.760    0.182   0.427   
stats_for_M3                       0.200   0.447     0.903    0.088   0.296   
stats_for_M5                       0.200   0.447     0.906    0.085   0.291   
stats_for_position                 0.130   0.360     1.182    0.198   0.445   
stats_for_length (x of gs)         0.093   0.306     0.797    0.183   0.428   

                           doctor_TH_old                  average_doctor_old  \
                                 average variance std Dev                      
stats_for_precision                0.742    0.077   0.278              0.720   
stats_for_recall                   0.562    0.057   0.239              0.469   
stats_for_f1-score                 0.640      NaN     NaN              0.564   
stats_for_f2-score                 0.591      NaN     NaN              0.503   
stats_for_NDCG                     0.736    0.056   0.236              0.642   
stats_for_M1                       0.747    0.189   0.435              0.659   
stats_for_M3                       0.880    0.105   0.325              0.771   
stats_for_M5                       0.885    0.102   0.319              0.774   
stats_for_position                 1.182    0.212   0.460              1.176   
stats_for_length (x of gs)         0.860    0.206   0.453              0.764   

                           average_doctor  
                                           
stats_for_precision                 0.746  
stats_for_recall                    0.467  
stats_for_f1-score                  0.571  
stats_for_f2-score                  0.503  
stats_for_NDCG                      0.656  
stats_for_M1                       

Results for experiment `disease_type=all failure-type-ignored=no-disease-found for app=best` is


Ada                  Ada_old                   \
                           average variance std Dev average variance std Dev   
stats_for_precision          0.436    0.064   0.254   0.446    0.073   0.270   
stats_for_recall             0.537    0.079   0.280   0.589    0.088   0.297   
stats_for_f1-score           0.481      NaN     NaN   0.508      NaN     NaN   
stats_for_f2-score           0.513      NaN     NaN   0.554      NaN     NaN   
stats_for_NDCG               0.614    0.096   0.309   0.636    0.105   0.324   
stats_for_M1                 0.524    0.249   0.499   0.543    0.248   0.498   
stats_for_M3                 0.742    0.192   0.438   0.717    0.203   0.451   
stats_for_M5                 0.783    0.170   0.412   0.766    0.179   0.423   
stats_for_position           1.522    0.795   0.892   1.515    0.948   0.974   
stats_for_length (x of gs)   1.377    0.319   0.565   1.577    0.462   0.680   

                              Avey                  Avey v2  ...  \
                           average variance std Dev average  ...   
stats_for_precision          0.403    0.063   0.250   0.405  ...   
stats_for_recall             0.628    0.112   0.334   0.643  ...   
stats_for_f1-score           0.491      NaN     NaN   0.497  ...   
stats_for_f2-score           0.565      NaN     NaN   0.575  ...   
stats_for_NDCG               0.657    0.112   0.334   0.691  ...   
stats_for_M1                 0.556    0.247   0.497   0.624  ...   
stats_for_M3                 0.752    0.187   0.432   0.791  ...   
stats_for_M5                 0.800    0.160   0.400   0.823  ...   
stats_for_position           1.499    0.866   0.930   1.382  ...   
stats_for_length (x of gs)   1.776    0.463   0.680   1.780  ...   

                           doctor_NJ_old         doctor_TH                   \
                                variance std Dev   average variance std Dev   
stats_for_precision                0.116   0.341     0.781    0.068   0.261   
stats_for_recall                   0.045   0.211     0.550    0.053   0.229   
stats_for_f1-score                   NaN     NaN     0.645      NaN     NaN   
stats_for_f2-score                   NaN     NaN     0.585      NaN     NaN   
stats_for_NDCG                     0.092   0.304     0.743    0.046   0.213   
stats_for_M1                       0.223   0.472     0.760    0.182   0.427   
stats_for_M3                       0.200   0.447     0.903    0.088   0.296   
stats_for_M5                       0.200   0.447     0.906    0.085   0.291   
stats_for_position                 0.130   0.360     1.182    0.198   0.445   
stats_for_length (x of gs)         0.093   0.306     0.797    0.183   0.428   

                           doctor_TH_old                  average_doctor_old  \
                                 average variance std Dev                      
stats_for_precision                0.742    0.077   0.278              0.720   
stats_for_recall                   0.562    0.057   0.239              0.469   
stats_for_f1-score                 0.640      NaN     NaN              0.564   
stats_for_f2-score                 0.591      NaN     NaN              0.503   
stats_for_NDCG                     0.736    0.056   0.236              0.642   
stats_for_M1                       0.747    0.189   0.435              0.659   
stats_for_M3                       0.880    0.105   0.325              0.771   
stats_for_M5                       0.885    0.102   0.319              0.774   
stats_for_position                 1.182    0.212   0.460              1.176   
stats_for_length (x of gs)         0.860    0.206   0.453              0.764   

                           average_doctor  
                                           
stats_for_precision                 0.746  
stats_for_recall                    0.467  
stats_for_f1-score                  0.571  
stats_for_f2-score                  0.503  
stats_for_NDCG                      0.656  
stats_for_M1                       